### Ahora con la formula de Borovicka

In [1]:
from scipy import optimize, stats
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
from tqdm import tqdm

In [8]:
X0, Y0, a0 = float(724), float(472), float(1*np.pi/4) #x=724 parece una mejor opcion

In [137]:
def construct_radio(C, A, F):
    def r(x, y):
        return C * ( np.sqrt( (x-X0)**2 + (y-Y0)**2 ) + A*(y-X0)*np.cos(F-a0) - A*(x-X0)*np.sin(F-a0) )
    return r

def construct_u(C, A, F, V, S, D, P, Q):
    def u(x, y):
        r = construct_radio(C, A, F)
        return V*r(x, y) + S*(np.e**(D*r(x,y)) - 1) + P*(np.e**(Q*r(x,y)**2) - 1) 
    return u

def construct_b(E):
    def b(x, y):
        return a0 - E + np.arctan2((y - Y0),(x - X0))
    return b

def construct_altura(C, A, F, V, S, D, P, Q, E, ep):
    def z(x, y):
        u = construct_u(C, A, F, V, S, D, P, Q)
        b = construct_b(E)
        return np.arccos( np.cos(u(x,y))*np.cos(ep) - np.sin(u(x,y))*np.sin(ep)*np.cos(b(x,y)) )
    return z

def construct_altura_deg(C, A, F, V, S, D, P, Q, E, ep):
    def z(x, y):
        u = construct_u(C, A, F, V, S, D, P, Q)
        b = construct_b(E)
        return 90 - np.rad2deg( np.arccos( np.cos(u(x,y))*np.cos(ep) - np.sin(u(x,y))*np.sin(ep)*np.cos(b(x,y)) ) )
    return z

def construct_azimuth(C, A, F, V, S, D, P, Q, E, ep):
    def az(x, y):
        u = construct_u(C, A, F, V, S, D, P, Q)
        b = construct_b(E)
        z = construct_altura(C, A, F, V, S, D, P, Q, E, ep)
        return np.arcsin( np.sin(b(x,y))*np.sin(u(x,y))/np.sin(z(x,y)) ) + E
    return az

def construct_azimuth_deg(C, A, F, V, S, D, P, Q, E, ep):
    def az(x, y):
        u = construct_u(C, A, F, V, S, D, P, Q)
        b = construct_b(E)
        z = construct_altura(C, A, F, V, S, D, P, Q, E, ep)
        return np.rad2deg( np.arcsin( np.sin(b(x,y))*np.sin(u(x,y))/np.sin(z(x,y)) ) + E )
    return az

In [138]:
def plot_plano(plano):
    x = np.linspace(0, 1200, 100)
    y = np.linspace(0, 900, 100)
    X, Y = np.meshgrid(x, y)
    Z = plano(X, Y)
    fig,ax=plt.subplots(1,1)
    cp = ax.contourf(X, Y, Z, 10)
    fig.colorbar(cp) # Add a colorbar to a plot
    ax.set_title('Toda una linea que minimiza y=mx+n')
    plt.gca().invert_yaxis()
    ax.set_xlabel('x')
    ax.set_ylabel('y')
    plt.show()

def plot_altura(vector):
    plano = construct_altura_deg(*vector)
    plot_plano(plano)
    
def plot_azimuth(vector):
    plano = construct_azimuth_deg(*vector)
    plot_plano(plano)

In [139]:
def drop_outlayers_by_center(pixtab_df, x0, y0, Z_VALUE = 0.5):
    
    X_MIN = 250
    X_MAX = 1250
    Y_MIN = 0
    Y_MAX = 950
    MAX_RADIO = 500
    RADIO_STEPS = 2000
    query_str = "{}<=x<={} and {}<=y<={}".format(X_MIN, X_MAX,
                                                            Y_MIN, Y_MAX)
    data = pixtab_df.dropna(thresh = 7).query(query_str)
    
    r_list = []
    for indx in data.index:
        x = data.at[indx,"x"]
        y = data.at[indx,"y"]
        r = np.sqrt((x - x0)**2 + (y - y0)**2)
        r_list.append(r)
    data["radio"] = r_list

    rstep = MAX_RADIO/(RADIO_STEPS-1)
    r_range = np.linspace(0, MAX_RADIO, RADIO_STEPS)
    pbar = tqdm(total=RADIO_STEPS, desc="Droping Outlayers")
    new_df = []
    for r in r_range:
        query = "radio > {} and radio <= {}".format(r, r+rstep)
        df_circle = data.query(query).dropna()
        if len(df_circle)==1:
            new_df.append(df_circle)
        elif len(df_circle)>1:
            z = stats.zscore(df_circle.alt.values)
            indx = np.where(np.abs(z) < Z_VALUE)
            new_df.append(df_circle.loc[df_circle.index.values[indx]])
        pbar.update()
    pbar.close()
    new_df = pd.concat(new_df, ignore_index=True)
    return new_df

# out = drop_outlayers_by_center(data, X0, Y0)
# out
# out["xcentroid"] = out["x"]
# out["ycentroid"] = out["y"]
# out.to_csv("drop_outlayer.dat", sep=' ', index=False)
# plt.gca().invert_yaxis()
# plt.scatter(out.x.values, out.y.values, c=out.alt.values, s=0.01)

In [140]:
def construct_alt_xi(x, y, z):
    def xi(C, A, F, V, S, D, P, Q, E, ep):
        alt_teorico = construct_altura_deg(C, A, F, V, S, D, P, Q, E, ep)
        return (z - alt_teorico(x, y))**2
    return xi

def construct_acumulate_alt_xi(x_list, y_list, z_list):
    def acumulate_xi(params):
        C, A, F, V, S, D, P, Q, E, ep = params
        suma_xi = 0
        for x, y, z in zip(x_list, y_list, z_list):
            xi = construct_alt_xi(int(x), int(y), int(z))
            suma_xi += xi(C, A, F, V, S, D, P, Q, E, ep)
        pbar.update()
        return suma_xi
    return acumulate_xi

def construct_az_xi(x, y, z):
    def xi(C, A, F, V, S, D, P, Q, E, ep):
        az_teorico = construct_azimuth_deg(C, A, F, V, S, D, P, Q, E, ep)
        return (z - az_teorico(x, y))**2
    return xi

def construct_acumulate_az_xi(x_list, y_list, z_list):
    def acumulate_xi(params):
        C, A, F, V, S, D, P, Q, E, ep = params
        suma_xi = 0
        for x, y, z in zip(x_list, y_list, z_list):
            xi = construct_az_xi(int(x), int(y), int(z))
            suma_xi += xi(C, A, F, V, S, D, P, Q, E, ep)
        pbar.update()
        return suma_xi
    return acumulate_xi

In [7]:
def amoeba(params, mega_alt_xi, mega_az_xi):
    new_alt_params = optimize.fmin(mega_alt_xi, params, maxfun=2200)
#     new_az_params = optimize.fmin(mega_az_xi, params, maxfun=110)
    return [new_alt_params]

In [53]:
%matplotlib qt

data = pd.read_csv("Data.pixtab", sep=" ")
data = data.dropna()
data = drop_outlayers_by_center(data, X0, Y0)
x_exp = data.x.values
y_exp = data.y.values
alt_catalogo = data.alt.values
az_catalogo = data.az.values
# plt.gca().invert_yaxis()
# plt.scatter(x_exp, y_exp, c=alt_catalogo, s=0.01)



Droping Outlayers:   0%|                                                                      | 0/2000 [00:00<?, ?it/s]

Droping Outlayers:   1%|▋                                                           | 24/2000 [00:00<00:08, 238.21it/s]

Droping Outlayers:   2%|█▍                                                          | 49/2000 [00:00<00:08, 239.04it/s]

Droping Outlayers:   4%|██▏                                                         | 73/2000 [00:00<00:08, 238.81it/s]

Droping Outlayers:   5%|██▉                                                         | 96/2000 [00:00<00:08, 235.59it/s]

Droping Outlayers:   6%|███▌                                                       | 119/2000 [00:00<00:08, 231.95it/s]

Droping Outlayers:   7%|████▏                                                      | 142/2000 [00:00<00:08, 230.16it/s]

Droping Outlayers:   8%|████▊                                                      | 165/2000 [00:00<00:08, 228.91it/s]

Droping Outlayers:   9%|█████▌

In [25]:
C, A, F = 0.07, 0.01, 1
V, S, D, P, Q = 0.03, 0.007, 0.09, 2.2*10**-6, 0.006
E, ep = 0, 0

mega_alt_xi = construct_acumulate_alt_xi(x_exp, y_exp, alt_catalogo)
mega_az_xi = construct_acumulate_az_xi(x_exp, y_exp, az_catalogo)
results_list = []

In [26]:
for i in range(4):
    pbar = tqdm(total=2200, desc="Aproximando altura y azimuth")
    results_list += amoeba([C,A,F,V,S,D,P,Q,E,ep], mega_alt_xi, mega_az_xi)
    pbar.close()
results_list[-1]


Aproximando altura y azimuth:   0%|                                                 | 1/2200 [00:03<2:19:04,  3.79s/it]

KeyboardInterrupt: 

### Resultados con la configuracion actual

Con centro $x=757$, $y=472$ y $a0=0$ y usando todos los datos

In [58]:
X0, Y0, a0 = float(757), float(472), float(0)

In [59]:
result1 = np.array([ 4.05411155*10**-2, -5.13000215*10**-2,  1.18306086,  8.18813843*10**-2,
       -3.63276373*10**-3, -1.22830557,  1.09298238*10**-5,  1.29796815*10**-2,
        2.09851909*10**-3,  5.53361549*10**-2])
result2 = np.array([ 2.90396335*10**-2, -1.36275018*10**-2, -2.42156457*10**-1,  1.14623453*10**-1,
       -6.22511285*10**-3, -4.72148386,  4.53040216*10**-5,  1.57578545*10**-2,
       -3.35189511*10**-2,  1.03652889*10**-1])
result3 = np.array([ 2.87039016*10**-2, -5.47881381*10**-3, -2.49778009*10**-1,  1.14866070*10**-1,
       -2.19097809*10**-2, -4.58387917*10**-1,  2.62567843*10**-4,  2.39744298*10**-2,
       -1.06146519*10**-1,  1.02486171*10**-1])
result4 = np.array([ 0.02863326, -0.00550686, -0.30656714,  0.11274438, -0.03916933,
       -0.29909259,  0.00547779,  0.01104806, -0.10624677,  0.1027069 ])
result5 = np.array([ 0.02896625, -0.00554929, -0.3355378 ,  0.11107163, -0.04046421,
       -0.29994853,  0.00962758,  0.00862338, -0.10597777,  0.10286461])

In [60]:
(mega_alt_xi(result1)/len(x_exp), mega_alt_xi(result2)/len(x_exp),
 mega_alt_xi(result3)/len(x_exp), mega_alt_xi(result4)/len(x_exp),
 mega_alt_xi(result5)/len(x_exp))


Aproximando altura y azimuth:   2%|█▏                                              | 53/2200 [41:53<5:31:56,  9.28s/it]

(3.417301236112704,
 2.776068690339051,
 2.7564699510172916,
 2.754597924132028,
 2.754326082216683)

No está bien quedarse con esto porque x0 está mal ahi, además a0 no puede ser 0

Con centro $x=724$, $y=472$ y $a0=\frac{-3\pi}{4}$

In [63]:
X0, Y0, a0 = float(724), float(472), float(-3*np.pi/4)

In [61]:
results_list_z05 = [np.array([ 4.88504077e-02,  2.02995372e-02,  3.51610379e-01,  6.82171007e-02,
         3.10608468e-03, -5.75141386e-05,  4.26865327e-06, -4.15889519e-03,
         2.21040767e-03,  1.47892726e-03]),
 np.array([ 4.88504077e-02,  2.02995372e-02,  3.51610379e-01,  6.82171007e-02,
         3.10608468e-03, -5.75141386e-05,  4.26865327e-06, -4.15889519e-03,
         2.21040767e-03,  1.47892726e-03]),
 np.array([ 4.88504077e-02,  2.02995372e-02,  3.51610379e-01,  6.82171007e-02,
         3.10608468e-03, -5.75141386e-05,  4.26865327e-06, -4.15889519e-03,
         2.21040767e-03,  1.47892726e-03]),
 np.array([ 4.88504077e-02,  2.02995372e-02,  3.51610379e-01,  6.82171007e-02,
         3.10608468e-03, -5.75141386e-05,  4.26865327e-06, -4.15889519e-03,
         2.21040767e-03,  1.47892726e-03])]
results_list_z1 = [np.array([ 6.68386793e-02,  2.11643138e-02,  3.95994947e-01,  4.97793056e-02,
        -1.98285373e-04,  3.95323036e-02,  1.77167244e-06,  8.38067924e-03,
         4.35828992e-04,  2.52528618e-03]),
 np.array([ 6.68386793e-02,  2.11643138e-02,  3.95994947e-01,  4.97793056e-02,
        -1.98285373e-04,  3.95323036e-02,  1.77167244e-06,  8.38067924e-03,
         4.35828992e-04,  2.52528618e-03]),
 np.array([ 6.68386793e-02,  2.11643138e-02,  3.95994947e-01,  4.97793056e-02,
        -1.98285373e-04,  3.95323036e-02,  1.77167244e-06,  8.38067924e-03,
         4.35828992e-04,  2.52528618e-03]),
 np.array([ 6.68386793e-02,  2.11643138e-02,  3.95994947e-01,  4.97793056e-02,
        -1.98285373e-04,  3.95323036e-02,  1.77167244e-06,  8.38067924e-03,
         4.35828992e-04,  2.52528618e-03])]

In [64]:
(mega_alt_xi(results_list_z05[-1])/len(x_exp), mega_alt_xi(results_list_z1[-1])/len(x_exp),
 mega_alt_xi(result3)/len(x_exp))


Aproximando altura y azimuth:   3%|█▎                                              | 59/2200 [44:28<8:26:06, 14.18s/it]

(2.810622513345362, 2.813157449737228, 31.782596665091102)

### Ahora intentaremos párametros de la manera Borovicka

#### Reduction types:

There are many types as mentioned in the section 2.2.3. of the paper.
However, IRED may be zero when entering REDSKY. Then the standard
reduction type 314 is used. The most usual types are

314 - V,S,D,P,Q kept at their standard values, other constants computed

334 - P,Q kept, C=1, other computed

354 - C=1, other computed (requires stars close to horizon)

311 - as 314 but A=0, F=0 (similarly 331, 351)

310 - as 311 but also epsilon=0, E=0 (similarly 330, 350)

319 - as 314 but epsilon,E,A,F kept at their initial values (similarly
      339, 359)

#### 314 - V,S,D,P,Q kept at their standard values, other constants computed

In [66]:
"""
Redefinimos el Xi para que no dependa de V,S,D,P,Q
Resultados con x0=724, y=472, a0=-3*np.pi/4
y habiendo reducido datos con z=05
"""
V, S, D, P, Q = results_list_z05[-1][3:8]
def construct_acumulate_alt_xi(x_list, y_list, z_list):
    def acumulate_xi(params):
        C, A, F, E, ep = params
        suma_xi = 0
        for x, y, z in zip(x_list, y_list, z_list):
            xi = construct_alt_xi(int(x), int(y), int(z))
            suma_xi += xi(C, A, F, V, S, D, P, Q, E, ep)
        pbar.update()
        return suma_xi
    return acumulate_xi

In [69]:
data = pd.read_csv("Data.pixtab", sep=" ")
data = data.dropna()
data = drop_outlayers_by_center(data, X0, Y0)
x = (data.x.values)
x_exp = data.x.values
y_exp = data.y.values
alt_catalogo = data.alt.values
az_catalogo = data.az.values
mega_alt_xi = construct_acumulate_alt_xi(x_exp, y_exp, alt_catalogo)
mega_az_xi = construct_acumulate_az_xi(x_exp, y_exp, az_catalogo)
results_list = []



Droping Outlayers:   0%|                                                                      | 0/2000 [00:00<?, ?it/s]

Droping Outlayers:   1%|▋                                                           | 22/2000 [00:00<00:09, 217.85it/s]

Droping Outlayers:   2%|█▎                                                          | 45/2000 [00:00<00:08, 218.93it/s]

Droping Outlayers:   3%|██                                                          | 67/2000 [00:00<00:08, 217.47it/s]

Droping Outlayers:   4%|██▋                                                         | 89/2000 [00:00<00:08, 217.76it/s]

Droping Outlayers:   6%|███▎                                                       | 111/2000 [00:00<00:08, 218.03it/s]

Droping Outlayers:   7%|███▉                                                       | 134/2000 [00:00<00:08, 220.03it/s]

Droping Outlayers:   8%|████▋                                                      | 158/2000 [00:00<00:08, 223.64it/s]

Droping Outlayers:   9%|█████▎

In [81]:
results_list += amoeba([C, A, F, E, ep], mega_alt_xi, mega_az_xi)
for i in range(3):
    pbar = tqdm(total=2200, desc="Aproximando altura y azimuth")
    results_list += amoeba(results_list[-1], mega_alt_xi, mega_az_xi)
    pbar.close()
results_list[-1]



Aproximando altura y azimuth:   0%|                                                           | 0/2200 [00:00<?, ?it/s]

Aproximando altura y azimuth:   0%|                                                 | 1/2200 [00:02<1:14:03,  2.02s/it]

Aproximando altura y azimuth:   0%|                                                 | 2/2200 [00:04<1:14:02,  2.02s/it]

Aproximando altura y azimuth:   0%|                                                 | 3/2200 [00:06<1:13:48,  2.02s/it]

Aproximando altura y azimuth:   0%|                                                 | 4/2200 [00:08<1:14:09,  2.03s/it]

Aproximando altura y azimuth:   0%|                                                 | 5/2200 [00:10<1:14:08,  2.03s/it]

Aproximando altura y azimuth:   0%|▏                                                | 6/2200 [00:12<1:14:27,  2.04s/it]

Aproximando altura y azimuth:   0%|▏                                                | 7/2200 [00:14<1:14:17,  2.03s/it]

Aproximando altura y azimuth: 

Aproximando altura y azimuth:   6%|██▊                                            | 134/2200 [04:29<1:09:20,  2.01s/it]

Aproximando altura y azimuth:   6%|██▉                                            | 135/2200 [04:31<1:09:11,  2.01s/it]

Aproximando altura y azimuth:   6%|██▉                                            | 136/2200 [04:33<1:09:06,  2.01s/it]

Aproximando altura y azimuth:   6%|██▉                                            | 137/2200 [04:35<1:08:55,  2.00s/it]

Aproximando altura y azimuth:   6%|██▉                                            | 138/2200 [04:37<1:09:05,  2.01s/it]

Aproximando altura y azimuth:   6%|██▉                                            | 139/2200 [04:39<1:08:53,  2.01s/it]

Aproximando altura y azimuth:   6%|██▉                                            | 140/2200 [04:41<1:08:52,  2.01s/it]

Aproximando altura y azimuth:   6%|███                                            | 141/2200 [04:43<1:08:51,  2.01s/it]

Aproximando altura y azimuth:   

Aproximando altura y azimuth:  12%|█████▋                                         | 268/2200 [08:58<1:04:19,  2.00s/it]

Aproximando altura y azimuth:  12%|█████▋                                         | 269/2200 [09:00<1:04:34,  2.01s/it]

Aproximando altura y azimuth:  12%|█████▊                                         | 270/2200 [09:02<1:04:27,  2.00s/it]

Aproximando altura y azimuth:  12%|█████▊                                         | 271/2200 [09:04<1:04:18,  2.00s/it]

Aproximando altura y azimuth:  12%|█████▊                                         | 272/2200 [09:06<1:04:06,  1.99s/it]

Aproximando altura y azimuth:  12%|█████▊                                         | 273/2200 [09:08<1:04:09,  2.00s/it]

Aproximando altura y azimuth:  12%|█████▊                                         | 274/2200 [09:10<1:04:08,  2.00s/it]

Aproximando altura y azimuth:  12%|█████▉                                         | 275/2200 [09:12<1:04:08,  2.00s/it]

Aproximando altura y azimuth:  1

Aproximando altura y azimuth:  18%|████████▌                                      | 402/2200 [13:27<1:01:02,  2.04s/it]

Aproximando altura y azimuth:  18%|████████▌                                      | 403/2200 [13:29<1:02:26,  2.08s/it]

Aproximando altura y azimuth:  18%|████████▋                                      | 404/2200 [13:31<1:01:36,  2.06s/it]

Aproximando altura y azimuth:  18%|████████▋                                      | 405/2200 [13:33<1:00:59,  2.04s/it]

Aproximando altura y azimuth:  18%|████████▋                                      | 406/2200 [13:35<1:00:50,  2.03s/it]

Aproximando altura y azimuth:  18%|████████▋                                      | 407/2200 [13:37<1:00:39,  2.03s/it]

Aproximando altura y azimuth:  19%|████████▋                                      | 408/2200 [13:39<1:00:28,  2.02s/it]

Aproximando altura y azimuth:  19%|████████▋                                      | 409/2200 [13:41<1:00:19,  2.02s/it]

Aproximando altura y azimuth:  1

Optimization terminated successfully.
         Current function value: 5870.324582
         Iterations: 315
         Function evaluations: 524


...

Aproximando altura y azimuth:  12%|█████▋                                         | 267/2200 [08:57<1:05:18,  2.03s/it]

Aproximando altura y azimuth:  12%|█████▋                                         | 268/2200 [08:59<1:04:54,  2.02s/it]

Aproximando altura y azimuth:  12%|█████▋                                         | 269/2200 [09:01<1:04:47,  2.01s/it]

Aproximando altura y azimuth:  12%|█████▊                                         | 270/2200 [09:03<1:04:33,  2.01s/it]

Aproximando altura y azimuth:  12%|█████▊                                         | 271/2200 [09:05<1:04:28,  2.01s/it]

Aproximando altura y azimuth:  12%|█████▊                                         | 272/2200 [09:07<1:04:35,  2.01s/it]

Aproximando altura y azimuth:  12%|█████▊                                         | 273/2200 [09:09<1:04:28,  2.01s/it]

Aproximando altura y azimuth:  12%|█████▊                                         | 274/2200 [09:11<1:04:17,  2.00s/it]

Aproximando altura y azimuth:  1

Aproximando altura y azimuth:  18%|████████▌                                      | 401/2200 [13:27<1:00:35,  2.02s/it]

Aproximando altura y azimuth:  18%|████████▌                                      | 402/2200 [13:29<1:00:17,  2.01s/it]

Aproximando altura y azimuth:  18%|████████▌                                      | 403/2200 [13:32<1:00:33,  2.02s/it]

Aproximando altura y azimuth:  18%|████████▋                                      | 404/2200 [13:33<1:00:08,  2.01s/it]

Aproximando altura y azimuth:  18%|████████▋                                      | 405/2200 [13:35<1:00:01,  2.01s/it]

Aproximando altura y azimuth:  18%|████████▋                                      | 406/2200 [13:38<1:00:09,  2.01s/it]

Aproximando altura y azimuth:  18%|████████▋                                      | 407/2200 [13:40<1:00:14,  2.02s/it]

Aproximando altura y azimuth:  19%|████████▋                                      | 408/2200 [13:42<1:00:07,  2.01s/it]

Aproximando altura y azimuth:  1

Optimization terminated successfully.
         Current function value: 5870.324582
         Iterations: 315
         Function evaluations: 524


Aproximando altura y azimuth:  24%|███████████▋                                     | 524/2200 [17:35<56:16,  2.01s/it]


array([0.04884979, 0.02030483, 0.35248629, 0.00538374, 0.00149506])

In [142]:
data = pd.read_csv("Data.pixtab", sep=" ")
data = data.dropna()
x_exp = data.x.values
y_exp = data.y.values
alt_catalogo = data.alt.values
az_catalogo = data.az.values
mega_alt_xi = construct_acumulate_alt_xi(x_exp, y_exp, alt_catalogo)

In [133]:
result_314 = np.array([0.04884978986903654, 0.020304825896093035, 0.35248628545828664, 0.0682171007,
                         0.00310608468, -5.75141386e-05, 4.26865327e-06, -0.00415889519,
                           0.005383738310580881, 0.0014950622892165601])

In [143]:
mega_alt_xi(result_314)/len(x_exp)

2.206150388035022

#### Probamos con mover x0, y0, a0

In [95]:
"""
Agregamos como parametros variables x0, y0, a0
"""
def construct_radio(C, A, F, X0, Y0, a0):
    def r(x, y):
        return C * ( np.sqrt( (x-X0)**2 + (y-Y0)**2 ) + A*(y-X0)*np.cos(F-a0) - A*(x-X0)*np.sin(F-a0) )
    return r

def construct_u(C, A, F, V, S, D, P, Q, X0, Y0, a0):
    def u(x, y):
        r = construct_radio(C, A, F, X0, Y0, a0)
        return V*r(x, y) + S*(np.e**(D*r(x,y)) - 1) + P*(np.e**(Q*r(x,y)**2) - 1) 
    return u

def construct_b(E, X0, Y0, a0):
    def b(x, y):
        return a0 - E + np.arctan2((y - Y0),(x - X0))
    return b

def construct_altura(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0):
    def z(x, y):
        u = construct_u(C, A, F, V, S, D, P, Q, X0, Y0, a0)
        b = construct_b(E, X0, Y0, a0)
        return np.arccos( np.cos(u(x,y))*np.cos(ep) - np.sin(u(x,y))*np.sin(ep)*np.cos(b(x,y)) )
    return z

def construct_altura_deg(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0):
    def z(x, y):
        u = construct_u(C, A, F, V, S, D, P, Q, X0, Y0, a0)
        b = construct_b(E, X0, Y0, a0)
        return 90 - np.rad2deg( np.arccos( np.cos(u(x,y))*np.cos(ep) - np.sin(u(x,y))*np.sin(ep)*np.cos(b(x,y)) ) )
    return z

def construct_azimuth(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0):
    def az(x, y):
        u = construct_u(C, A, F, V, S, D, P, Q, X0, Y0, a0)
        b = construct_b(E, X0, Y0, a0)
        z = construct_altura(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0)
        return np.arcsin( np.sin(b(x,y))*np.sin(u(x,y))/np.sin(z(x,y)) ) + E
    return az

def construct_azimuth_deg(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0):
    def az(x, y):
        u = construct_u(C, A, F, V, S, D, P, Q, X0, Y0, a0)
        b = construct_b(E, X0, Y0, a0)
        z = construct_altura(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0)
        return np.rad2deg( np.arcsin( np.sin(b(x,y))*np.sin(u(x,y))/np.sin(z(x,y)) ) + E )
    return az

In [96]:
def construct_alt_xi(x, y, z):
    def xi(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0):
        alt_teorico = construct_altura_deg(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0)
        return (z - alt_teorico(x, y))**2
    return xi

def construct_acumulate_alt_xi(x_list, y_list, z_list):
    def acumulate_xi(params):
        C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0 = params
        suma_xi = 0
        for x, y, z in zip(x_list, y_list, z_list):
            xi = construct_alt_xi(int(x), int(y), int(z))
            suma_xi += xi(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0)
        pbar.update()
        return suma_xi
    return acumulate_xi

def construct_az_xi(x, y, z):
    def xi(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0):
        az_teorico = construct_azimuth_deg(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0)
        return (z - az_teorico(x, y))**2
    return xi

def construct_acumulate_az_xi(x_list, y_list, z_list):
    def acumulate_xi(params):
        C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0 = params
        suma_xi = 0
        for x, y, z in zip(x_list, y_list, z_list):
            xi = construct_az_xi(int(x), int(y), int(z))
            suma_xi += xi(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0)
        pbar.update()
        return suma_xi
    return acumulate_xi

In [102]:
data = pd.read_csv("Data.pixtab", sep=" ")
data = data.dropna()
x_exp = data.x.values
y_exp = data.y.values
alt_catalogo = data.alt.values
az_catalogo = data.az.values
mega_alt_xi = construct_acumulate_alt_xi(x_exp, y_exp, alt_catalogo)
results_list = []

init_params = np.array([0.04884978986903654, 0.020304825896093035, 0.35248628545828664, 0.0682171007,
                         0.00310608468, -5.75141386e-05, 4.26865327e-06, -0.00415889519,
                           0.005383738310580881, 0.0014950622892165601, float(724), float(472), float(-3*np.pi/4)])

In [104]:
pbar = tqdm(total=2200, desc="Aproximando altura y azimuth")
results_list += amoeba(init_params, mega_alt_xi, mega_az_xi)
pbar.close()
for i in range(3):
    pbar = tqdm(total=2200, desc="Aproximando altura y azimuth")
    results_list += amoeba(results_list[-1], mega_alt_xi, mega_az_xi)
    pbar.close()
results_list[-1]





Aproximando altura y azimuth:   0%|                                                           | 0/2200 [00:00<?, ?it/s]



Aproximando altura y azimuth:   0%|                                                 | 1/2200 [00:05<3:35:44,  5.89s/it]



Aproximando altura y azimuth:   0%|                                                 | 2/2200 [00:11<3:34:57,  5.87s/it]



Aproximando altura y azimuth:   0%|                                                 | 3/2200 [00:17<3:34:12,  5.85s/it]



Aproximando altura y azimuth:   0%|                                                 | 4/2200 [00:23<3:33:21,  5.83s/it]



Aproximando altura y azimuth:   0%|                                                 | 5/2200 [00:29<3:37:05,  5.93s/it]



Aproximando altura y azimuth:   0%|▏                                                | 6/2200 [00:35<3:39:15,  6.00s/it]



Aproximando altura y azimuth:   0%|▏                                                | 7/2200 [00:41<3:38:35,  5.98s/it]



Aproximando 

Aproximando altura y azimuth:   6%|██▊                                            | 132/2200 [12:45<3:19:41,  5.79s/it]



Aproximando altura y azimuth:   6%|██▊                                            | 133/2200 [12:51<3:19:06,  5.78s/it]



Aproximando altura y azimuth:   6%|██▊                                            | 134/2200 [12:56<3:18:38,  5.77s/it]



Aproximando altura y azimuth:   6%|██▉                                            | 135/2200 [13:02<3:18:54,  5.78s/it]



Aproximando altura y azimuth:   6%|██▉                                            | 136/2200 [13:08<3:18:23,  5.77s/it]



Aproximando altura y azimuth:   6%|██▉                                            | 137/2200 [13:14<3:17:59,  5.76s/it]



Aproximando altura y azimuth:   6%|██▉                                            | 138/2200 [13:19<3:18:13,  5.77s/it]



Aproximando altura y azimuth:   6%|██▉                                            | 139/2200 [13:25<3:18:20,  5.77s/it]



Aproximando altu

Aproximando altura y azimuth:  12%|█████▋                                         | 264/2200 [25:24<3:04:47,  5.73s/it]



Aproximando altura y azimuth:  12%|█████▋                                         | 265/2200 [25:30<3:05:34,  5.75s/it]



Aproximando altura y azimuth:  12%|█████▋                                         | 266/2200 [25:36<3:07:23,  5.81s/it]



Aproximando altura y azimuth:  12%|█████▋                                         | 267/2200 [25:42<3:10:39,  5.92s/it]



Aproximando altura y azimuth:  12%|█████▋                                         | 268/2200 [25:48<3:09:36,  5.89s/it]



Aproximando altura y azimuth:  12%|█████▋                                         | 269/2200 [25:54<3:10:52,  5.93s/it]



Aproximando altura y azimuth:  12%|█████▊                                         | 270/2200 [26:00<3:12:46,  5.99s/it]



Aproximando altura y azimuth:  12%|█████▊                                         | 271/2200 [26:06<3:13:39,  6.02s/it]



Aproximando altu

Aproximando altura y azimuth:  18%|████████▍                                      | 396/2200 [38:06<2:53:31,  5.77s/it]



Aproximando altura y azimuth:  18%|████████▍                                      | 397/2200 [38:12<2:53:26,  5.77s/it]



Aproximando altura y azimuth:  18%|████████▌                                      | 398/2200 [38:18<2:53:04,  5.76s/it]



Aproximando altura y azimuth:  18%|████████▌                                      | 399/2200 [38:24<2:52:48,  5.76s/it]



Aproximando altura y azimuth:  18%|████████▌                                      | 400/2200 [38:30<2:53:46,  5.79s/it]



Aproximando altura y azimuth:  18%|████████▌                                      | 401/2200 [38:35<2:53:17,  5.78s/it]



Aproximando altura y azimuth:  18%|████████▌                                      | 402/2200 [38:41<2:53:21,  5.78s/it]



Aproximando altura y azimuth:  18%|████████▌                                      | 403/2200 [38:47<2:52:55,  5.77s/it]



Aproximando altu

Aproximando altura y azimuth:  24%|███████████▎                                   | 528/2200 [50:50<2:40:39,  5.76s/it]



Aproximando altura y azimuth:  24%|███████████▎                                   | 529/2200 [50:56<2:40:24,  5.76s/it]



Aproximando altura y azimuth:  24%|███████████▎                                   | 530/2200 [51:01<2:40:01,  5.75s/it]



Aproximando altura y azimuth:  24%|███████████▎                                   | 531/2200 [51:07<2:39:33,  5.74s/it]



Aproximando altura y azimuth:  24%|███████████▎                                   | 532/2200 [51:13<2:40:17,  5.77s/it]



Aproximando altura y azimuth:  24%|███████████▍                                   | 533/2200 [51:19<2:39:57,  5.76s/it]



Aproximando altura y azimuth:  24%|███████████▍                                   | 534/2200 [51:24<2:39:58,  5.76s/it]



Aproximando altura y azimuth:  24%|███████████▍                                   | 535/2200 [51:30<2:39:36,  5.75s/it]



Aproximando altu

...

Aproximando altura y azimuth:  84%|██████████████████████████████████████▌       | 1847/2200 [3:00:06<34:07,  5.80s/it]



Aproximando altura y azimuth:  84%|██████████████████████████████████████▋       | 1848/2200 [3:00:12<33:55,  5.78s/it]



Aproximando altura y azimuth:  84%|██████████████████████████████████████▋       | 1849/2200 [3:00:18<33:52,  5.79s/it]



Aproximando altura y azimuth:  84%|██████████████████████████████████████▋       | 1850/2200 [3:00:24<33:57,  5.82s/it]



Aproximando altura y azimuth:  84%|██████████████████████████████████████▋       | 1851/2200 [3:00:30<33:54,  5.83s/it]



Aproximando altura y azimuth:  84%|██████████████████████████████████████▋       | 1852/2200 [3:00:35<33:46,  5.82s/it]



Aproximando altura y azimuth:  84%|██████████████████████████████████████▋       | 1853/2200 [3:00:41<33:33,  5.80s/it]



Aproximando altura y azimuth:  84%|██████████████████████████████████████▊       | 1854/2200 [3:00:47<33:24,  5.79s/it]



Aproximando altu

Aproximando altura y azimuth:  90%|█████████████████████████████████████████▍    | 1979/2200 [3:12:54<21:26,  5.82s/it]



Aproximando altura y azimuth:  90%|█████████████████████████████████████████▍    | 1980/2200 [3:13:00<21:24,  5.84s/it]



Aproximando altura y azimuth:  90%|█████████████████████████████████████████▍    | 1981/2200 [3:13:05<21:15,  5.82s/it]



Aproximando altura y azimuth:  90%|█████████████████████████████████████████▍    | 1982/2200 [3:13:11<21:06,  5.81s/it]



Aproximando altura y azimuth:  90%|█████████████████████████████████████████▍    | 1983/2200 [3:13:17<21:03,  5.82s/it]



Aproximando altura y azimuth:  90%|█████████████████████████████████████████▍    | 1984/2200 [3:13:23<20:55,  5.81s/it]



Aproximando altura y azimuth:  90%|█████████████████████████████████████████▌    | 1985/2200 [3:13:29<20:52,  5.83s/it]



Aproximando altura y azimuth:  90%|█████████████████████████████████████████▌    | 1986/2200 [3:13:35<20:43,  5.81s/it]



Aproximando altu

Aproximando altura y azimuth:  96%|████████████████████████████████████████████▏ | 2111/2200 [3:25:43<08:38,  5.83s/it]



Aproximando altura y azimuth:  96%|████████████████████████████████████████████▏ | 2112/2200 [3:25:49<08:33,  5.84s/it]



Aproximando altura y azimuth:  96%|████████████████████████████████████████████▏ | 2113/2200 [3:25:55<08:28,  5.84s/it]



Aproximando altura y azimuth:  96%|████████████████████████████████████████████▏ | 2114/2200 [3:26:01<08:21,  5.83s/it]



Aproximando altura y azimuth:  96%|████████████████████████████████████████████▏ | 2115/2200 [3:26:06<08:15,  5.83s/it]



Aproximando altura y azimuth:  96%|████████████████████████████████████████████▏ | 2116/2200 [3:26:12<08:11,  5.85s/it]



Aproximando altura y azimuth:  96%|████████████████████████████████████████████▎ | 2117/2200 [3:26:18<08:04,  5.84s/it]



Aproximando altura y azimuth:  96%|████████████████████████████████████████████▎ | 2118/2200 [3:26:24<07:58,  5.84s/it]



Aproximando altu

Aproximando altura y azimuth: 100%|██████████████████████████████████████████████| 2200/2200 [3:34:21<00:00,  5.85s/it]


array([ 4.37875766e-02,  5.19853314e-03,  1.05416567e+00,  7.33610329e-02,
       -5.24112025e-02, -1.39156740e-01,  4.41635759e-03,  4.71369350e-03,
        2.74820813e+00, -1.02665758e-01,  7.30572294e+02,  5.05444291e+02,
       -1.83144878e+00])

In [117]:
result_var_center = np.array([ 4.37875766e-02,  5.19853314e-03,  1.05416567e+00,  7.33610329e-02,
       -5.24112025e-02, -1.39156740e-01,  4.41635759e-03,  4.71369350e-03,
        2.74820813e+00, -1.02665758e-01,  7.30572294e+02,  5.05444291e+02,
       -1.83144878e+00])

In [107]:
mega_alt_xi(results_list[-1])/len(x_exp)

2.1548216119125754

Es curioso que el cenith lo posiciona en (731, 506)

#### Probaremos amoeba con azimut tambien

In [125]:
def amoeba(params, mega_alt_xi, mega_az_xi):
    new_alt_params = optimize.fmin(mega_alt_xi, params, maxfun=1100)
    new_az_params = optimize.fmin(mega_az_xi, params, maxfun=110)
    return [new_alt_params, new_az_params]

In [132]:
data = pd.read_csv("Data.pixtab", sep=" ")
data = data.dropna()
x_exp = data.x.values
y_exp = data.y.values
alt_catalogo = data.alt.values
az_catalogo = np.rad2deg(np.arccos(np.cos(np.deg2rad(data.az.values))))
mega_alt_xi = construct_acumulate_alt_xi(x_exp, y_exp, alt_catalogo)
mega_az_xi = construct_acumulate_az_xi(x_exp, y_exp, az_catalogo)
results_list = []

init_params = np.array([0.04884978986903654, 0.020304825896093035, 0.35248628545828664, 0.0682171007,
                         0.00310608468, -5.75141386e-05, 4.26865327e-06, -0.00415889519,
                           0.005383738310580881, 0.0014950622892165601, float(724), float(472), float(1*np.pi/4)])

In [ ]:
pbar = tqdm(total=2200, desc="Aproximando altura y azimuth")
results_list += amoeba(init_params, mega_alt_xi, mega_az_xi)
pbar.close()
for i in range(3):
    pbar = tqdm(total=2200, desc="Aproximando altura y azimuth")
    results_list += amoeba(results_list[-1], mega_alt_xi, mega_az_xi)
    pbar.close()
results_list[-1]







Aproximando altura y azimuth:   0%|                                                           | 0/2200 [00:00<?, ?it/s]





Aproximando altura y azimuth:   0%|                                                 | 1/2200 [00:05<3:33:40,  5.83s/it]





Aproximando altura y azimuth:   0%|                                                 | 2/2200 [00:11<3:32:46,  5.81s/it]





Aproximando altura y azimuth:   0%|                                                 | 3/2200 [00:17<3:32:16,  5.80s/it]





Aproximando altura y azimuth:   0%|                                                 | 4/2200 [00:23<3:32:04,  5.79s/it]





Aproximando altura y azimuth:   0%|                                                 | 5/2200 [00:28<3:31:36,  5.78s/it]





Aproximando altura y azimuth:   0%|▏                                                | 6/2200 [00:34<3:31:25,  5.78s/it]





Aproximando altura y azimuth:   0%|▏                                                | 7/2200 [00:40<3:31:13,  5.78s/it]

Aproximando altura y azimuth:   6%|██▊                                            | 130/2200 [12:24<3:17:40,  5.73s/it]





Aproximando altura y azimuth:   6%|██▊                                            | 131/2200 [12:30<3:17:30,  5.73s/it]





Aproximando altura y azimuth:   6%|██▊                                            | 132/2200 [12:36<3:17:31,  5.73s/it]





Aproximando altura y azimuth:   6%|██▊                                            | 133/2200 [12:42<3:19:04,  5.78s/it]





Aproximando altura y azimuth:   6%|██▊                                            | 134/2200 [12:47<3:18:43,  5.77s/it]





Aproximando altura y azimuth:   6%|██▉                                            | 135/2200 [12:53<3:18:26,  5.77s/it]





Aproximando altura y azimuth:   6%|██▉                                            | 136/2200 [12:59<3:18:34,  5.77s/it]





Aproximando altura y azimuth:   6%|██▉                                            | 137/2200 [13:05<3:18:24,  5.77s/it]







Aproximando altura y azimuth:  12%|█████▌                                         | 260/2200 [24:51<3:06:04,  5.75s/it]





Aproximando altura y azimuth:  12%|█████▌                                         | 261/2200 [24:57<3:07:36,  5.81s/it]





Aproximando altura y azimuth:  12%|█████▌                                         | 262/2200 [25:03<3:06:33,  5.78s/it]





Aproximando altura y azimuth:  12%|█████▌                                         | 263/2200 [25:09<3:06:29,  5.78s/it]





Aproximando altura y azimuth:  12%|█████▋                                         | 264/2200 [25:15<3:05:42,  5.76s/it]





Aproximando altura y azimuth:  12%|█████▋                                         | 265/2200 [25:20<3:06:00,  5.77s/it]





Aproximando altura y azimuth:  12%|█████▋                                         | 266/2200 [25:26<3:05:42,  5.76s/it]





Aproximando altura y azimuth:  12%|█████▋                                         | 267/2200 [25:32<3:05:53,  5.77s/it]







#### Probamos amoeba en azimut y altura con discriminacion de datos según centro

In [111]:
def construct_radio(C, A, F):
    def r(x, y):
        return C * ( np.sqrt( (x-X0)**2 + (y-Y0)**2 ) + A*(y-X0)*np.cos(F-a0) - A*(x-X0)*np.sin(F-a0) )
    return r

def construct_u(C, A, F, V, S, D, P, Q):
    def u(x, y):
        r = construct_radio(C, A, F)
        return V*r(x, y) + S*(np.e**(D*r(x,y)) - 1) + P*(np.e**(Q*r(x,y)**2) - 1) 
    return u

def construct_b(E):
    def b(x, y):
        return a0 - E + np.arctan2((y - Y0),(x - X0))
    return b

def construct_altura(C, A, F, V, S, D, P, Q, E, ep):
    def z(x, y):
        u = construct_u(C, A, F, V, S, D, P, Q)
        b = construct_b(E)
        return np.arccos( np.cos(u(x,y))*np.cos(ep) - np.sin(u(x,y))*np.sin(ep)*np.cos(b(x,y)) )
    return z

def construct_altura_deg(C, A, F, V, S, D, P, Q, E, ep):
    def z(x, y):
        u = construct_u(C, A, F, V, S, D, P, Q)
        b = construct_b(E)
        return 90 - np.rad2deg( np.arccos( np.cos(u(x,y))*np.cos(ep) - np.sin(u(x,y))*np.sin(ep)*np.cos(b(x,y)) ) )
    return z

def construct_azimuth(C, A, F, V, S, D, P, Q, E, ep):
    def az(x, y):
        u = construct_u(C, A, F, V, S, D, P, Q)
        b = construct_b(E)
        z = construct_altura(C, A, F, V, S, D, P, Q, E, ep)
        return np.arcsin( np.sin(b(x,y))*np.sin(u(x,y))/np.sin(z(x,y)) ) + E
    return az

def construct_azimuth_deg(C, A, F, V, S, D, P, Q, E, ep):
    def az(x, y):
        u = construct_u(C, A, F, V, S, D, P, Q)
        b = construct_b(E)
        z = construct_altura(C, A, F, V, S, D, P, Q, E, ep)
        return np.rad2deg( np.arcsin( np.sin(b(x,y))*np.sin(u(x,y))/np.sin(z(x,y)) ) + E )
    return az

def construct_alt_xi(x, y, z):
    def xi(C, A, F, V, S, D, P, Q, E, ep):
        alt_teorico = construct_altura_deg(C, A, F, V, S, D, P, Q, E, ep)
        return (z - alt_teorico(x, y))**2
    return xi

def construct_acumulate_alt_xi(x_list, y_list, z_list):
    def acumulate_xi(params):
        C, A, F, V, S, D, P, Q, E, ep = params
        suma_xi = 0
        for x, y, z in zip(x_list, y_list, z_list):
            xi = construct_alt_xi(int(x), int(y), int(z))
            suma_xi += xi(C, A, F, V, S, D, P, Q, E, ep)
        pbar.update()
        return suma_xi
    return acumulate_xi

def construct_az_xi(x, y, z):
    def xi(C, A, F, V, S, D, P, Q, E, ep):
        az_teorico = construct_azimuth_deg(C, A, F, V, S, D, P, Q, E, ep)
        return (z - az_teorico(x, y))**2
    return xi

def construct_acumulate_az_xi(x_list, y_list, z_list):
    def acumulate_xi(params):
        C, A, F, V, S, D, P, Q, E, ep = params
        suma_xi = 0
        for x, y, z in zip(x_list, y_list, z_list):
            xi = construct_az_xi(int(x), int(y), int(z))
            suma_xi += xi(C, A, F, V, S, D, P, Q, E, ep)
        pbar.update()
        return suma_xi
    return acumulate_xi

def amoeba(params, mega_alt_xi, mega_az_xi):
    new_alt_params = optimize.fmin(mega_alt_xi, params, maxfun=110)
    new_az_params = optimize.fmin(mega_az_xi, params, maxfun=110)
    return [new_alt_params, new_az_params]

In [41]:
X0, Y0, a0 = float(731), float(472), float(1*np.pi/4)

In [42]:
data = pd.read_csv("Data.pixtab", sep=" ")
data = data.dropna()
data = drop_outlayers_by_center(data, X0, Y0)
x_exp = data.x.values
y_exp = data.y.values
alt_catalogo = data.alt.values
az_catalogo = np.rad2deg(np.arccos(np.cos(np.deg2rad(data.az.values))))
mega_alt_xi = construct_acumulate_alt_xi(x_exp, y_exp, alt_catalogo)
mega_az_xi = construct_acumulate_az_xi(x_exp, y_exp, az_catalogo)
results_list = []

init_params = np.array([0.04884978986903654, 0.020304825896093035, 0.35248628545828664, 0.0682171007,
                         0.00310608468, -5.75141386e-05, 4.26865327e-06, -0.00415889519,
                           0.005383738310580881, 0.0014950622892165601])



Droping Outlayers:   0%|                                                                      | 0/2000 [00:00<?, ?it/s]

Droping Outlayers:   1%|▊                                                           | 25/2000 [00:00<00:08, 245.75it/s]

Droping Outlayers:   2%|█▍                                                          | 49/2000 [00:00<00:08, 241.97it/s]

Droping Outlayers:   4%|██▏                                                         | 73/2000 [00:00<00:08, 240.14it/s]

Droping Outlayers:   5%|██▉                                                         | 97/2000 [00:00<00:08, 237.43it/s]

Droping Outlayers:   6%|███▌                                                       | 121/2000 [00:00<00:07, 235.60it/s]

Droping Outlayers:   7%|████▏                                                      | 144/2000 [00:00<00:07, 233.37it/s]

Droping Outlayers:   8%|████▉                                                      | 168/2000 [00:00<00:07, 233.45it/s]

Droping Outlayers:  10%|█████▋

Droping Outlayers:  78%|█████████████████████████████████████████████▎            | 1564/2000 [00:06<00:01, 221.55it/s]

Droping Outlayers:  79%|██████████████████████████████████████████████            | 1587/2000 [00:07<00:01, 217.84it/s]

Droping Outlayers:  80%|██████████████████████████████████████████████▋           | 1610/2000 [00:07<00:01, 219.00it/s]

Droping Outlayers:  82%|███████████████████████████████████████████████▎          | 1633/2000 [00:07<00:01, 221.73it/s]

Droping Outlayers:  83%|████████████████████████████████████████████████          | 1656/2000 [00:07<00:01, 223.02it/s]

Droping Outlayers:  84%|████████████████████████████████████████████████▋         | 1680/2000 [00:07<00:01, 226.09it/s]

Droping Outlayers:  85%|█████████████████████████████████████████████████▍        | 1703/2000 [00:07<00:01, 226.11it/s]

Droping Outlayers:  86%|██████████████████████████████████████████████████        | 1726/2000 [00:07<00:01, 220.27it/s]

Droping Outlayers:  87%|████████

In [53]:
pbar = tqdm(total=220, desc="Aproximando altura y azimuth")
results_list += amoeba(init_params, mega_alt_xi, mega_az_xi)
pbar.close()
for i in range(3):
    pbar = tqdm(total=220, desc="Aproximando altura y azimuth")
    results_list += amoeba(results_list[-1], mega_alt_xi, mega_az_xi)
    pbar.close()
results_list[-1]



Aproximando altura y azimuth:   0%|                                                            | 0/220 [00:00<?, ?it/s]

Aproximando altura y azimuth:   0%|▏                                                   | 1/220 [00:02<07:20,  2.01s/it]

Aproximando altura y azimuth:   1%|▍                                                   | 2/220 [00:04<07:18,  2.01s/it]

Aproximando altura y azimuth:   1%|▋                                                   | 3/220 [00:06<07:15,  2.01s/it]

Aproximando altura y azimuth:   2%|▉                                                   | 4/220 [00:08<07:14,  2.01s/it]

Aproximando altura y azimuth:   2%|█▏                                                  | 5/220 [00:10<07:11,  2.01s/it]

Aproximando altura y azimuth:   3%|█▍                                                  | 6/220 [00:12<07:10,  2.01s/it]

Aproximando altura y azimuth:   3%|█▋                                                  | 7/220 [00:14<07:09,  2.02s/it]

Aproximando altura y azimuth: 

Aproximando altura y azimuth:  30%|███████████████▌                                   | 67/220 [02:14<05:05,  2.00s/it]

Aproximando altura y azimuth:  31%|███████████████▊                                   | 68/220 [02:16<05:03,  2.00s/it]

Aproximando altura y azimuth:  31%|███████████████▉                                   | 69/220 [02:18<05:01,  2.00s/it]

Aproximando altura y azimuth:  32%|████████████████▏                                  | 70/220 [02:20<04:59,  2.00s/it]

Aproximando altura y azimuth:  32%|████████████████▍                                  | 71/220 [02:22<04:57,  2.00s/it]

Aproximando altura y azimuth:  33%|████████████████▋                                  | 72/220 [02:24<04:57,  2.01s/it]

Aproximando altura y azimuth:  33%|████████████████▉                                  | 73/220 [02:26<04:55,  2.01s/it]

Aproximando altura y azimuth:  34%|█████████████████▏                                 | 74/220 [02:28<04:52,  2.00s/it]

Aproximando altura y azimuth:  3



Aproximando altura y azimuth:  50%|█████████████████████████▏                        | 111/220 [03:42<04:10,  2.30s/it]

Aproximando altura y azimuth:  51%|█████████████████████████▍                        | 112/220 [03:45<04:31,  2.51s/it]

Aproximando altura y azimuth:  51%|█████████████████████████▋                        | 113/220 [03:49<04:46,  2.68s/it]

Aproximando altura y azimuth:  52%|█████████████████████████▉                        | 114/220 [03:52<04:54,  2.78s/it]

Aproximando altura y azimuth:  52%|██████████████████████████▏                       | 115/220 [03:55<05:00,  2.86s/it]

Aproximando altura y azimuth:  53%|██████████████████████████▎                       | 116/220 [03:58<05:02,  2.91s/it]

Aproximando altura y azimuth:  53%|██████████████████████████▌                       | 117/220 [04:01<05:03,  2.95s/it]

Aproximando altura y azimuth:  54%|██████████████████████████▊                       | 118/220 [04:04<05:02,  2.97s/it]

Aproximando altura y azimuth: 

Aproximando altura y azimuth:  81%|████████████████████████████████████████▍         | 178/220 [07:05<02:05,  3.00s/it]

Aproximando altura y azimuth:  81%|████████████████████████████████████████▋         | 179/220 [07:08<02:02,  3.00s/it]

Aproximando altura y azimuth:  82%|████████████████████████████████████████▉         | 180/220 [07:11<01:59,  3.00s/it]

Aproximando altura y azimuth:  82%|█████████████████████████████████████████▏        | 181/220 [07:14<01:57,  3.00s/it]

Aproximando altura y azimuth:  83%|█████████████████████████████████████████▎        | 182/220 [07:17<01:53,  3.00s/it]

Aproximando altura y azimuth:  83%|█████████████████████████████████████████▌        | 183/220 [07:20<01:51,  3.01s/it]

Aproximando altura y azimuth:  84%|█████████████████████████████████████████▊        | 184/220 [07:23<01:48,  3.02s/it]

Aproximando altura y azimuth:  84%|██████████████████████████████████████████        | 185/220 [07:26<01:45,  3.02s/it]

Aproximando altura y azimuth:  8

Aproximando altura y azimuth: 100%|██████████████████████████████████████████████████| 220/220 [09:13<00:00,  2.51s/it]


Aproximando altura y azimuth:   0%|                                                            | 0/220 [00:00<?, ?it/s]

Aproximando altura y azimuth:   0%|▏                                                   | 1/220 [00:01<07:08,  1.96s/it]

Aproximando altura y azimuth:   1%|▍                                                   | 2/220 [00:03<07:07,  1.96s/it]

Aproximando altura y azimuth:   1%|▋                                                   | 3/220 [00:05<07:07,  1.97s/it]

Aproximando altura y azimuth:   2%|▉                                                   | 4/220 [00:07<07:06,  1.97s/it]

Aproximando altura y azimuth:   2%|█▏                                                  | 5/220 [00:09<07:05,  1.98s/it]

Aproximando altura y azimuth:   3%|█▍                                                  | 6/220 [00:11<07:08,  2.00s/it]

Aproximando altura y azimuth:  

...

Aproximando altura y azimuth:  30%|███████████████▌                                   | 67/220 [02:16<05:12,  2.04s/it]

Aproximando altura y azimuth:  31%|███████████████▊                                   | 68/220 [02:18<05:07,  2.02s/it]

Aproximando altura y azimuth:  31%|███████████████▉                                   | 69/220 [02:20<05:03,  2.01s/it]

Aproximando altura y azimuth:  32%|████████████████▏                                  | 70/220 [02:22<04:59,  2.00s/it]

Aproximando altura y azimuth:  32%|████████████████▍                                  | 71/220 [02:24<04:57,  1.99s/it]

Aproximando altura y azimuth:  33%|████████████████▋                                  | 72/220 [02:26<04:53,  1.99s/it]

Aproximando altura y azimuth:  33%|████████████████▉                                  | 73/220 [02:28<04:54,  2.01s/it]

Aproximando altura y azimuth:  34%|█████████████████▏                                 | 74/220 [02:30<04:52,  2.00s/it]

Aproximando altura y azimuth:  3



Aproximando altura y azimuth:  50%|█████████████████████████▏                        | 111/220 [03:45<04:09,  2.29s/it]

Aproximando altura y azimuth:  51%|█████████████████████████▍                        | 112/220 [03:48<04:32,  2.52s/it]

Aproximando altura y azimuth:  51%|█████████████████████████▋                        | 113/220 [03:52<04:53,  2.74s/it]

Aproximando altura y azimuth:  52%|█████████████████████████▉                        | 114/220 [03:55<05:08,  2.91s/it]

Aproximando altura y azimuth:  52%|██████████████████████████▏                       | 115/220 [03:58<05:13,  2.99s/it]

Aproximando altura y azimuth:  53%|██████████████████████████▎                       | 116/220 [04:01<05:13,  3.02s/it]

Aproximando altura y azimuth:  53%|██████████████████████████▌                       | 117/220 [04:04<05:13,  3.04s/it]

Aproximando altura y azimuth:  54%|██████████████████████████▊                       | 118/220 [04:07<05:12,  3.06s/it]

Aproximando altura y azimuth: 

Aproximando altura y azimuth:  80%|████████████████████████████████████████▏         | 177/220 [07:10<02:13,  3.10s/it]

Aproximando altura y azimuth:  81%|████████████████████████████████████████▍         | 178/220 [07:13<02:08,  3.07s/it]

Aproximando altura y azimuth:  81%|████████████████████████████████████████▋         | 179/220 [07:16<02:05,  3.06s/it]

Aproximando altura y azimuth:  82%|████████████████████████████████████████▉         | 180/220 [07:19<02:02,  3.05s/it]

Aproximando altura y azimuth:  82%|█████████████████████████████████████████▏        | 181/220 [07:22<01:58,  3.04s/it]

Aproximando altura y azimuth:  83%|█████████████████████████████████████████▎        | 182/220 [07:25<01:55,  3.03s/it]

Aproximando altura y azimuth:  83%|█████████████████████████████████████████▌        | 183/220 [07:28<01:51,  3.03s/it]

Aproximando altura y azimuth:  84%|█████████████████████████████████████████▊        | 184/220 [07:31<01:50,  3.07s/it]

Aproximando altura y azimuth:  8

Aproximando altura y azimuth: 100%|██████████████████████████████████████████████████| 220/220 [09:22<00:00,  2.55s/it]


array([ 4.08361981e-02, -1.15309654e-01,  1.28986593e-01,  1.63198059e-02,
        4.10621499e-03, -7.32014079e-05,  1.58768211e-05, -6.93893607e-03,
        3.54640930e-05,  5.59019786e-03])

In [82]:
result_mini_az = np.array([ 4.08361981e-02, -1.15309654e-01,  1.28986593e-01,  1.63198059e-02,
        4.10621499e-03, -7.32014079e-05,  1.58768211e-05, -6.93893607e-03,
        3.54640930e-05,  5.59019786e-03])

#### ahora usamos 314 pero con mover x0 e y0, ademas de discriminar datos

In [157]:
def construct_radio(C, A, F, X0, Y0, a0):
    def r(x, y):
        return C * ( np.sqrt( (x-X0)**2 + (y-Y0)**2 ) + A*(y-X0)*np.cos(F-a0) - A*(x-X0)*np.sin(F-a0) )
    return r

def construct_u(C, A, F, V, S, D, P, Q, X0, Y0, a0):
    def u(x, y):
        r = construct_radio(C, A, F, X0, Y0, a0)
        return V*r(x, y) + S*(np.e**(D*r(x,y)) - 1) + P*(np.e**(Q*r(x,y)**2) - 1) 
    return u

def construct_b(E, X0, Y0, a0):
    def b(x, y):
        return a0 - E + np.arctan2((y - Y0),(x - X0))
    return b

def construct_altura(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0):
    def z(x, y):
        u = construct_u(C, A, F, V, S, D, P, Q, X0, Y0, a0)
        b = construct_b(E, X0, Y0, a0)
        return np.arccos( np.cos(u(x,y))*np.cos(ep) - np.sin(u(x,y))*np.sin(ep)*np.cos(b(x,y)) )
    return z

def construct_altura_deg(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0):
    def z(x, y):
        u = construct_u(C, A, F, V, S, D, P, Q, X0, Y0, a0)
        b = construct_b(E, X0, Y0, a0)
        return 90 - np.rad2deg( np.arccos( np.cos(u(x,y))*np.cos(ep) - np.sin(u(x,y))*np.sin(ep)*np.cos(b(x,y)) ) )
    return z

def construct_azimuth(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0):
    def az(x, y):
        u = construct_u(C, A, F, V, S, D, P, Q, X0, Y0, a0)
        b = construct_b(E, X0, Y0, a0)
        z = construct_altura(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0)
        return np.arcsin( np.sin(b(x,y))*np.sin(u(x,y))/np.sin(z(x,y)) ) + E
    return az

def construct_azimuth_deg(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0):
    def az(x, y):
        u = construct_u(C, A, F, V, S, D, P, Q, X0, Y0, a0)
        b = construct_b(E, X0, Y0, a0)
        z = construct_altura(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0)
        return np.rad2deg( np.arcsin( np.sin(b(x,y))*np.sin(u(x,y))/np.sin(z(x,y)) ) + E ) + 90
    return az

######################################################################################################

def construct_alt_xi(x, y, z):
    def xi(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0):
        alt_teorico = construct_altura_deg(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0)
        return (z - alt_teorico(x, y))**2
    return xi

def construct_acumulate_alt_xi(x_list, y_list, z_list, ctes = None):
    def acumulate_xi(params):
        V, S, D, P, Q, a0 = ctes
        C, A, F, E, ep, X0, Y0 = params
        suma_xi = 0
        for x, y, z in zip(x_list, y_list, z_list):
            xi = construct_alt_xi(int(x), int(y), int(z))
            suma_xi += xi(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0)
        pbar.update()
        return suma_xi
    return acumulate_xi

def construct_az_xi(x, y, z):
    def xi(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0):
        az_teorico = construct_azimuth_deg(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0)
        return (z - az_teorico(x, y))**2
    return xi

def construct_acumulate_az_xi(x_list, y_list, z_list, ctes = None):
    def acumulate_xi(params):
        V, S, D, P, Q, a0 = ctes
        C, A, F, E, ep, X0, Y0 = params
        suma_xi = 0
        for x, y, z in zip(x_list, y_list, z_list):
            xi = construct_az_xi(int(x), int(y), int(z))
            suma_xi += xi(C, A, F, V, S, D, P, Q, E, ep, X0, Y0, a0)
        pbar.update()
        return suma_xi
    return acumulate_xi

######################################################################################################

def amoeba(params, mega_alt_xi, mega_az_xi):
    new_alt_params = optimize.fmin(mega_alt_xi, params, maxfun=1100)
    new_az_params = optimize.fmin(mega_az_xi, params, maxfun=1100)
    return [new_alt_params, new_az_params]

In [167]:
X0, Y0 = float(724), float(472)
V, S, D, P, Q, a0 = (0.0682171007, 0.00310608468, -5.75141386e-05,
                             4.26865327e-06, -0.00415889519, float(1*np.pi/4))


params_ctes = [V, S, D, P, Q, a0]

data = pd.read_csv("Data.pixtab", sep=" ")
data = data.dropna()
data = drop_outlayers_by_center(data, X0, Y0, 2)
x_exp = data.x.values
y_exp = data.y.values
alt_catalogo = data.alt.values
az_catalogo = np.rad2deg(np.arccos(np.cos(np.deg2rad(data.az.values))))
mega_alt_xi = construct_acumulate_alt_xi(x_exp, y_exp, alt_catalogo, params_ctes)
mega_az_xi = construct_acumulate_az_xi(x_exp, y_exp, az_catalogo, params_ctes)
results_list = []

init_params = np.array([0.04884978986903654, 0.020304825896093035, 0.35248628545828664,
        0.005383738310580881, 0.0014950622892165601, X0, Y0])







Droping Outlayers:   0%|                                                                      | 0/2000 [00:00<?, ?it/s]





Droping Outlayers:   1%|▋                                                           | 22/2000 [00:00<00:09, 217.97it/s]





Droping Outlayers:   2%|█▎                                                          | 45/2000 [00:00<00:08, 218.94it/s]





Droping Outlayers:   3%|██                                                          | 68/2000 [00:00<00:08, 220.21it/s]





Droping Outlayers:   4%|██▋                                                         | 90/2000 [00:00<00:08, 220.09it/s]





Droping Outlayers:   6%|███▎                                                       | 112/2000 [00:00<00:08, 219.44it/s]





Droping Outlayers:   7%|███▉                                                       | 134/2000 [00:00<00:08, 217.09it/s]





Droping Outlayers:   8%|████▋                                                      | 157/2000 [00:00<00:08, 218.24it/s]

Droping Outlayers:  71%|█████████████████████████████████████████▍                | 1428/2000 [00:06<00:02, 217.72it/s]





Droping Outlayers:  72%|██████████████████████████████████████████                | 1450/2000 [00:06<00:02, 217.78it/s]





Droping Outlayers:  74%|██████████████████████████████████████████▋               | 1473/2000 [00:06<00:02, 218.19it/s]





Droping Outlayers:  75%|███████████████████████████████████████████▎              | 1495/2000 [00:07<00:02, 218.22it/s]





Droping Outlayers:  76%|███████████████████████████████████████████▉              | 1517/2000 [00:07<00:02, 217.47it/s]





Droping Outlayers:  77%|████████████████████████████████████████████▋             | 1539/2000 [00:07<00:02, 216.87it/s]





Droping Outlayers:  78%|█████████████████████████████████████████████▎            | 1562/2000 [00:07<00:02, 217.59it/s]





Droping Outlayers:  79%|█████████████████████████████████████████████▉            | 1584/2000 [00:07<00:01, 218.24it/s]







In [168]:
mega_alt_xi(init_params)/len(x_exp)






Aproximando altura y azimuth:   2%|▊                                               | 39/2200 [03:29<7:16:00, 12.11s/it]

7.602674574571149

In [169]:
pbar = tqdm(total=2200, desc="Aproximando altura y azimuth")
results_list += amoeba(init_params, mega_alt_xi, mega_az_xi)
pbar.close()
for i in range(3):
    pbar = tqdm(total=2200, desc="Aproximando altura y azimuth")
    results_list += amoeba(results_list[-1], mega_alt_xi, mega_az_xi)
    pbar.close()
results_list[-1]







Aproximando altura y azimuth:   0%|                                                           | 0/2200 [00:00<?, ?it/s]





Aproximando altura y azimuth:   0%|                                                 | 1/2200 [00:05<3:37:13,  5.93s/it]





Aproximando altura y azimuth:   0%|                                                 | 2/2200 [00:11<3:37:15,  5.93s/it]





Aproximando altura y azimuth:   0%|                                                 | 3/2200 [00:17<3:36:53,  5.92s/it]





Aproximando altura y azimuth:   0%|                                                 | 4/2200 [00:23<3:36:49,  5.92s/it]





Aproximando altura y azimuth:   0%|                                                 | 5/2200 [00:29<3:35:54,  5.90s/it]





Aproximando altura y azimuth:   0%|▏                                                | 6/2200 [00:35<3:34:43,  5.87s/it]





Aproximando altura y azimuth:   0%|▏                                                | 7/2200 [00:40<3:31:46,  5.79s/it]

Aproximando altura y azimuth:   3%|█▍                                              | 65/2200 [06:08<3:21:56,  5.67s/it]





Aproximando altura y azimuth:   3%|█▍                                              | 66/2200 [06:14<3:21:19,  5.66s/it]





Aproximando altura y azimuth:   3%|█▍                                              | 67/2200 [06:20<3:20:54,  5.65s/it]





Aproximando altura y azimuth:   3%|█▍                                              | 68/2200 [06:25<3:20:10,  5.63s/it]





Aproximando altura y azimuth:   3%|█▌                                              | 69/2200 [06:31<3:20:03,  5.63s/it]





Aproximando altura y azimuth:   3%|█▌                                              | 70/2200 [06:37<3:20:10,  5.64s/it]





Aproximando altura y azimuth:   3%|█▌                                              | 71/2200 [06:42<3:19:35,  5.62s/it]





Aproximando altura y azimuth:   3%|█▌                                              | 72/2200 [06:48<3:20:54,  5.66s/it]







Aproximando altura y azimuth:   6%|██▊                                            | 130/2200 [12:17<3:20:48,  5.82s/it]





Aproximando altura y azimuth:   6%|██▊                                            | 131/2200 [12:23<3:18:46,  5.76s/it]





Aproximando altura y azimuth:   6%|██▊                                            | 132/2200 [12:29<3:20:12,  5.81s/it]





Aproximando altura y azimuth:   6%|██▊                                            | 133/2200 [12:34<3:18:20,  5.76s/it]





Aproximando altura y azimuth:   6%|██▊                                            | 134/2200 [12:40<3:16:27,  5.71s/it]





Aproximando altura y azimuth:   6%|██▉                                            | 135/2200 [12:46<3:19:30,  5.80s/it]





Aproximando altura y azimuth:   6%|██▉                                            | 136/2200 [12:51<3:18:43,  5.78s/it]





Aproximando altura y azimuth:   6%|██▉                                            | 137/2200 [12:57<3:17:57,  5.76s/it]







Aproximando altura y azimuth:   9%|████▏                                          | 195/2200 [18:26<3:08:19,  5.64s/it]





Aproximando altura y azimuth:   9%|████▏                                          | 196/2200 [18:32<3:08:32,  5.64s/it]





Aproximando altura y azimuth:   9%|████▏                                          | 197/2200 [18:38<3:08:07,  5.64s/it]





Aproximando altura y azimuth:   9%|████▏                                          | 198/2200 [18:43<3:08:27,  5.65s/it]





Aproximando altura y azimuth:   9%|████▎                                          | 199/2200 [18:49<3:08:12,  5.64s/it]





Aproximando altura y azimuth:   9%|████▎                                          | 200/2200 [18:55<3:08:11,  5.65s/it]





Aproximando altura y azimuth:   9%|████▎                                          | 201/2200 [19:00<3:08:19,  5.65s/it]





Aproximando altura y azimuth:   9%|████▎                                          | 202/2200 [19:06<3:08:06,  5.65s/it]







Aproximando altura y azimuth:  12%|█████▌                                         | 260/2200 [24:34<3:01:51,  5.62s/it]





Aproximando altura y azimuth:  12%|█████▌                                         | 261/2200 [24:40<3:01:54,  5.63s/it]





Aproximando altura y azimuth:  12%|█████▌                                         | 262/2200 [24:45<3:01:54,  5.63s/it]





Aproximando altura y azimuth:  12%|█████▌                                         | 263/2200 [24:51<3:02:55,  5.67s/it]





Aproximando altura y azimuth:  12%|█████▋                                         | 264/2200 [24:57<3:03:03,  5.67s/it]





Aproximando altura y azimuth:  12%|█████▋                                         | 265/2200 [25:02<3:02:13,  5.65s/it]





Aproximando altura y azimuth:  12%|█████▋                                         | 266/2200 [25:08<3:01:35,  5.63s/it]





Aproximando altura y azimuth:  12%|█████▋                                         | 267/2200 [25:14<3:03:44,  5.70s/it]







...

Aproximando altura y azimuth:  68%|█████████████████████████████▊              | 1492/2200 [2:41:05<1:43:05,  8.74s/it]





Aproximando altura y azimuth:  68%|█████████████████████████████▊              | 1493/2200 [2:41:14<1:42:54,  8.73s/it]





Aproximando altura y azimuth:  68%|█████████████████████████████▉              | 1494/2200 [2:41:23<1:42:48,  8.74s/it]





Aproximando altura y azimuth:  68%|█████████████████████████████▉              | 1495/2200 [2:41:32<1:43:05,  8.77s/it]





Aproximando altura y azimuth:  68%|█████████████████████████████▉              | 1496/2200 [2:41:40<1:42:44,  8.76s/it]





Aproximando altura y azimuth:  68%|█████████████████████████████▉              | 1497/2200 [2:41:49<1:42:24,  8.74s/it]





Aproximando altura y azimuth:  68%|█████████████████████████████▉              | 1498/2200 [2:41:58<1:42:09,  8.73s/it]





Aproximando altura y azimuth:  68%|█████████████████████████████▉              | 1499/2200 [2:42:07<1:41:57,  8.73s/it]







Aproximando altura y azimuth:  71%|███████████████████████████████▏            | 1557/2200 [2:50:36<1:34:56,  8.86s/it]





Aproximando altura y azimuth:  71%|███████████████████████████████▏            | 1558/2200 [2:50:44<1:34:20,  8.82s/it]





Aproximando altura y azimuth:  71%|███████████████████████████████▏            | 1559/2200 [2:50:53<1:34:02,  8.80s/it]

Optimization terminated successfully.
         Current function value: 1159011.364795
         Iterations: 159
         Function evaluations: 458


Aproximando altura y azimuth:  71%|███████████████████████████████▏            | 1559/2200 [2:50:53<1:10:15,  6.58s/it]


array([2.40589404e-05, 3.61690281e-02, 1.96327429e+00, 1.54666808e-03,
       9.74578715e-06, 7.33556599e+02, 4.74724744e+02])

In [171]:
result_314_var_center = np.array([2.40589404e-05, 3.61690281e-02, 1.96327429e+00, 0.0682171007, 0.00310608468, -5.75141386e-05,
                             4.26865327e-06, -0.00415889519, 1.54666808e-03,
       9.74578715e-06, 7.33556599e+02, 4.74724744e+02, float(1*np.pi/4)])

In [174]:
plot_azimuth(result_314_var_center)

In [156]:
plot_azimuth([0.04884978986903654, 0.020304825896093035, 0.35248628545828664,V, S, D, P, Q,
        0.005383738310580881, 0.0014950622892165601, X0, Y0, a0])

# Otros

In [130]:
X0, Y0, a0 = float(724), float(472), float(-3*np.pi/4)
data = pd.read_csv("Data.pixtab", sep=" ")
data = data.dropna()
# data = drop_outlayers_by_center(data, X0, Y0)
x_exp = data.x.values
y_exp = data.y.values
alt_catalogo = data.alt.values
az_catalogo = np.rad2deg(np.arccos(np.cos(np.deg2rad(data.az.values))))
mega_alt_xi = construct_acumulate_alt_xi(x_exp, y_exp, alt_catalogo)
mega_az_xi = construct_acumulate_az_xi(x_exp, y_exp, az_catalogo)
results_list = []

init_params = np.array([0.04884978986903654, 0.020304825896093035, 0.35248628545828664, 0.0682171007,
                         0.00310608468, -5.75141386e-05, 4.26865327e-06, -0.00415889519,
                           0.005383738310580881, 0.0014950622892165601])

In [129]:
plot_altura([4.37875766e-02,  5.19853314e-03,  1.05416567e+00,V, S, D, P, Q,2.74820813e+00, -1.02665758e-01, X0, Y0,float(-3*np.pi/4)])

In [103]:
A = 1
def asd():
    print(A)

In [107]:
A =34
asd()

34
